# Transformer Anatomy


Este notebook é baseado no terceiro capítulo do livro [Natural Language Processing with Transformers](https://www.amazon.com/Natural-Language-Processing-Transformers-Applications/dp/1098103246) 

1. [The Transformer Architecture](#The-Transformer-Architecture)
2. [The Encoder](#The-Encoder)
3. [Self-Attention](#Self-Attention)
4. [Demystifying Queries, Keys, and Values](#Demystifying-Queries,-Keys,-and-Values)
5. [Dot Product attention](#Dot-Product-attention)
6. [Multi-headed attention](#Multi-headed-attention)
7. [The Feed-Forward Layer](#The-Feed-Forward-Layer)
8. [Layer Normalization](#Layer-Normalization)
9. [Positional Embeddings](#Positional-Embeddings)
10. [Full Transformer Encoder](#Full-transformer-encoder)
11. [Adding a Classification Head](#Adding-a-Classification-Head)
12. [The Decoder](#The-Decoder)
13. [The Transformer Tree of Life](#The-Transformer-Tree-of-Life)

In [1]:
# Uncomment and run this cell if you're on Colab or Kaggle
!git clone https://github.com/nlp-with-transformers/notebooks.git
%cd notebooks
from install import *
install_requirements()

/bin/bash: /opt/conda/lib/libtinfo.so.6: no version information available (required by /bin/bash)
Cloning into 'notebooks'...
remote: Enumerating objects: 526, done.
remote: Counting objects: 100% (526/526), done.
remote: Compressing objects: 100% (289/289), done.
remote: Total 526 (delta 251), reused 480 (delta 231), pack-reused 0
Receiving objects: 100% (526/526), 29.30 MiB | 24.12 MiB/s, done.
Resolving deltas: 100% (251/251), done.
/kaggle/working/notebooks
⏳ Installing base requirements ...
✅ Base requirements installed!
⏳ Installing Git LFS ...
✅ Git LFS installed!


In [ ]:
#hide
from utils import *
setup_chapter()

# The Transformer Architecture

A arquitetura transformer é um tipo de rede neural usada para tarefas de processamento de linguagem natural, como tradução de idiomas e classificação de texto. Ela utiliza uma abordagem única chamada autoatenção, que permite ao modelo focar em diferentes partes do texto de entrada e ponderar sua importância. Os transformers consistem em dois componentes principais: o codificador e o decodificador. O codificador lê o texto de entrada e gera uma representação que captura o significado do texto, enquanto o decodificador utiliza essa representação para gerar o texto de saída. Os transformers se tornaram muito populares devido à sua capacidade de processar sequências longas de texto de forma eficiente e ao seu desempenho em uma ampla gama de tarefas de processamento de linguagem natural.

<img src="https://raw.githubusercontent.com/nlp-with-transformers/notebooks/48e4a5e5c44b86e1593c0945a49af9675cfd7158/images/chapter03_transformer-encoder-decoder.png" width="500">


# The Encoder

No processamento de linguagem natural, o codificador é uma parte da arquitetura transformer responsável por compreender e interpretar o significado do texto. Ele recebe uma sequência de palavras (como uma frase) e a converte em uma representação mais abstrata e estruturada que captura as informações importantes no texto.

Pense nele como uma pessoa que lê uma história e a resume para outra pessoa. O codificador lê as palavras no texto (assim como a pessoa lendo a história) e depois resume as informações importantes em uma forma mais curta e organizada (como a saída do codificador). A saída do codificador é então passada para outra parte da arquitetura transformer, o decodificador, que pode usá-la para realizar várias tarefas de processamento de linguagem natural.

<img src="https://raw.githubusercontent.com/nlp-with-transformers/notebooks/48e4a5e5c44b86e1593c0945a49af9675cfd7158/images/chapter03_encoder-zoom.png" width="500">


# Self-Attention

Autoatenção é uma operação matemática que permite a um computador focar em diferentes partes de uma sequência de informações, como palavras em uma frase. Esta operação calcula quão importante cada palavra em uma sequência é em relação a todas as outras palavras na sequência.

A definição formal de autoatenção envolve a multiplicação de cada vetor de entrada por três diferentes matrizes de pesos para produzir consultas, chaves e valores. Esses vetores são então multiplicados entre si para obter um escore para cada palavra na sequência. Os escores são usados para ponderar os valores e obter uma soma ponderada, que representa a saída final da operação de autoatenção.

Em termos mais simples, a autoatenção é uma maneira para um computador prestar atenção em diferentes partes de uma frase, e isso é feito atribuindo uma pontuação a cada palavra com base em quão importante ela é no contexto das outras palavras na frase.

<img src="https://raw.githubusercontent.com/nlp-with-transformers/notebooks/48e4a5e5c44b86e1593c0945a49af9675cfd7158/images/chapter03_contextualized-embedding.png" width="700">


In [2]:
%%javascript
require.config({
  paths: {
      d3: '//cdnjs.cloudflare.com/ajax/libs/d3/3.4.8/d3.min',
      jquery: '//ajax.googleapis.com/ajax/libs/jquery/2.0.0/jquery.min',
  }
});

<IPython.core.display.Javascript object>

In [3]:
#hide_output
from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

model_ckpt = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model = BertModel.from_pretrained(model_ckpt)
text = "time flies like an arrow"
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

Downloading:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/226k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/455k [00:00<?, ?B/s]

100%|██████████| 440473133/440473133 [00:16<00:00, 26976725.50B/s]


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Demystifying Queries, Keys, and Values

<img src="https://raw.githubusercontent.com/nlp-with-transformers/notebooks/48e4a5e5c44b86e1593c0945a49af9675cfd7158/images/chapter03_attention-ops.png" width="700">


| Conceito | Explicação para uma criança | Definição Formal | Exemplo |
|---------|-------------------------------|-------------------|---------|
| Query | Uma pergunta que queremos responder | No mecanismo de atenção, a consulta é um dos três vetores de entrada (junto com Key e o Value) usados para calcular a saída. | Em traduação, a query pode ser a última palavra que foi gerada. |
| Key | Uma chave que destranca uma resposta | No mecanismo de atenção, a chave é um dos três vetores de entrada (junto com a Query e Value) usados para calcular a saída. | Em tradução, Key pode ser todas as palavras na sequência de entrada. |
| Value | A resposta para a nossa pergunta | No mecanismo de Atenção, o valor é um dos três vetores de entrada (junto com Query e Key) usado para computar a saída. | Em Traduação, o valor pode ser todas as palavras da sequência de entrada traduzidas na na linguagem de saída. |

In [ ]:
# hide
from transformers import AutoTokenizer
model_ckpt = "bert-base-uncased"
text = "time flies like an arrow"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)

Existem as perguntas, cada número representa uma palavra.

In [4]:
inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False)
inputs.input_ids

tensor([[ 2051, 10029,  2066,  2019,  8612]])

In [5]:
from torch import nn
from transformers import AutoConfig

config = AutoConfig.from_pretrained(model_ckpt)
token_emb = nn.Embedding(config.vocab_size, config.hidden_size)
token_emb

Embedding(30522, 768)

O ``config.vocab_size`` são os números de palavras únicas no modelo

O ``config.hidden_size`` é o tamanho das camadas ocultas na rede (independente da sua entrada)

As saídas são o batch_size, o número de palavras que eu tenho, e o número de camadas ocultas no modelo.

In [6]:
inputs_embeds = token_emb(inputs.input_ids)
inputs_embeds.size()

torch.Size([1, 5, 768])

Por simplicidade ``query``, ``key``, ``value``, são definidas igualmente, mas na realidade esses valores são diferentes no modelo

In [7]:
import torch
from math import sqrt 

query = key = value = inputs_embeds
dim_k = key.size(-1)
scores = torch.bmm(query, key.transpose(1,2)) / sqrt(dim_k)
scores.size()

torch.Size([1, 5, 5])

In [8]:
import torch.nn.functional as F

weights = F.softmax(scores, dim=-1)
weights.sum(dim=-1)

tensor([[1., 1., 1., 1., 1.]], grad_fn=<SumBackward1>)

In [9]:
attn_outputs = torch.bmm(weights, value)
attn_outputs.shape

torch.Size([1, 5, 768])

# Dot Product attention

A atenção por produto escalar é uma maneira para o transformer decidir quais palavras em uma frase ou sequência são as mais importantes para entender o significado dessa frase ou sequência. Funciona comparando cada palavra com todas as outras palavras na sequência e atribuindo a cada palavra uma pontuação com base em quão relevante ela é para as outras palavras. Isso é feito usando uma função matemática chamada produto escalar, que é apenas uma maneira sofisticada de multiplicar dois números juntos e somar os resultados.

Formalmente, a atenção por produto escalar calcula o produto escalar de um vetor de consulta e um vetor de chave, o que gera uma única pontuação que representa o quão bem a consulta corresponde à chave. Isso é então dividido pela raiz quadrada da dimensionalidade do vetor de chave, o que ajuda a manter as pontuações de ficarem muito grandes ou muito pequenas. Finalmente, a pontuação resultante é passada por uma função softmax para transformá-la em uma distribuição de probabilidade, que pode ser usada para ponderar os valores em um vetor de valores. Os valores ponderados são então somados para produzir um único vetor de saída, que representa a importância de cada palavra na sequência para entender o significado dessa sequência.

# Dot Product attention code

In [10]:
def scaled_dot_product_attention(query, key, value):
    """
    Computes the scaled dot product attention scores for a batch of queries, keys and values.
    
    Args:
        query: A tensor of shape (batch_size, query_len, embed_dim) containing the query vectors.
        key: A tensor of shape (batch_size, key_len, embed_dim) containing the key vectors.
        value: A tensor of shape (batch_size, value_len, embed_dim) containing the value vectors.

    Returns:
        A tensor of shape (batch_size, query_len, embed_dim) containing the weighted sum of values using the attention scores.
    """
    # Get the size of the last dimension of the query tensor
    dim_k = query.size(-1)
    
    # Compute the dot product of the query and key tensors 
    # using batch matrix multiplication
    # tf equivalent is tf.matmul
    scores = torch.bmm(query, key.transpose(1,2))
    
    # Scale the scores by the square root of the dimension of the key vectors
    scores = scores / torch.sqrt(torch.tensor(dim_k, dtype=torch.float32))
    
    # Apply the softmax function to the scores along the last dimension
    # to obtain the attention weights for each query
    weights = F.softmax(scores, dim=-1)
    
    # Compute the weighted sum of the value vectors using the attention weights
    # using batch matrix multiplication
    output = torch.bmm(weights, value)
    
    return output

# Multi-headed attention

🤖 Nos Transformers, a atenção multi-cabeça é uma maneira para o modelo examinar suas entradas de diferentes ângulos, e então compartilham as informações entre si e chegam a um resultado final.

A atenção multi-cabeça pode ser comparada a um Eletrocardiograma (ECG), no qual sensores são colocados em diferentes partes do seu corpo para monitorar a atividade elétrica do seu coração a partir de diferentes perspectivas, que são então combinadas para criar uma imagem completa da saúde do seu coração e interpretadas por um médico com o diagnóstico final.

**Why do we need more than one head?**

 - Para ser capaz de focar em vários aspectos ao mesmo tempo
 - A função softmax para uma cabeça tende a focar principalmente em um aspecto de semelhança

### Intuição

🤖 Nos Transformers, a atenção multi-cabeça é uma maneira para o modelo examinar suas entradas de diferentes ângulos, e então compartilham as informações entre si e chegam a um resultado final.

⚕ ➕ 🤖 A atenção multi-cabeça pode ser comparada a um Eletrocardiograma (ECG), no qual sensores são colocados em diferentes partes do seu corpo para monitorar a atividade elétrica do seu coração a partir de diferentes perspectivas, que são então combinadas para criar uma imagem completa da saúde do seu coração e interpretadas por um médico com o diagnóstico final.

<img src="https://user-images.githubusercontent.com/46135649/221360403-e964e9ea-9b79-41e4-b16a-d02cf568b687.png" width="400" height="50">



# Multi-head attention code

In [11]:
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        """
        Initialize the attention head layer.

        Args:
            embed_dim (int): The input embedding dimension size.
            head_dim (int): The dimension size of each attention head.
        """
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)  # Linear layer for query projection
        self.k = nn.Linear(embed_dim, head_dim)  # Linear layer for key projection
        self.v = nn.Linear(embed_dim, head_dim)  # Linear layer for value projection
        
    def forward(self, hidden_state):
        """
        Perform the attention head computation.

        Args:
            hidden_state (torch.Tensor): The input hidden state tensor.

        Returns:
            torch.Tensor: The output attention tensor.
        """
        # Compute the attention scores using scaled dot product attention
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state))
        
        return attn_outputs


Aqui estamos inicializando para aplicar a multiplicação de matriz aos vetores de incorporação.

Em termos simples: estamos inicializando uma transformação linear de nossa Consulta, Chave e Valor usando um tamanho de lote igual à dimensão de incorporação embed_dim (camadas ocultas no modelo - Bert geralmente tem 768 camadas ocultas), enquanto a dimensão de entrada head_dim é o número de dimensão para o qual estamos projetando (geralmente um múltiplo de embed_dim. Bert geralmente tem 12 cabeças de atenção), dividimos as camadas ocultas pela cabeça de atenção e obtemos o head_dim 768/12 = 64

Assim é como ficaria com os valores

```python
class AttentionHead(nn.Module):
    bert_hidden_layers = 768
    bert_att_head = 12
    head_dim = bert_hidden_layers // bert_att_head
    def __init__(self, embed_dim=bert_hidden_layers, head_dim=head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)
        
    def forward(self, hidden_state):
        attn_outputs = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state))
        return attn_outputs
```

Agora que a cabeça de atenção foi construída, vamos concatenar as saídas de cada uma para implementar a camada completa de atenção multi-cabeça.

In [12]:
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        """
        Initializes the MultiHeadAttention module.
        Args:
            config: a transformers.PretrainedConfig instance containing model configuration.
        """
        super().__init__()
        embed_dim = config.hidden_size
        num_heads = config.num_attention_heads
        head_dim = embed_dim // num_heads
        
        # Create a list of attention heads
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
        )
        
        # Final linear layer to combine the output of all attention heads
        self.output_linear = nn.Linear(embed_dim, embed_dim)

    def forward(self, hidden_state):
        """
        Computes multi-head self-attention over the input sequence.
        Args:
            hidden_state: input sequence of shape (batch_size, seq_len, hidden_size)
        Returns:
            Output of the multi-head self-attention operation, of shape (batch_size, seq_len, hidden_size).
        """
        # Apply attention head to each hidden state tensor
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        
        # Combine the output of all attention heads using a final linear layer
        x = self.output_linear(x)
        return x


Vamos testar e ver como funciona

In [13]:
multihead_attn = MultiHeadAttention(config)
attn_output = multihead_attn(inputs_embeds)
attn_output.size()

torch.Size([1, 5, 768])

Funciona!

Agora vamos visualizar a attention para dois diferentes uso da palavra "flies"

In [14]:
from bertviz import head_view
from transformers import AutoModel

model = AutoModel.from_pretrained(model_ckpt, output_attentions=True)

sentence_a = "time flies like an arrow"
sentence_b = "fruit flies like a banana"

viz_inputs = tokenizer(sentence_a, sentence_b, return_tensors='pt')
attention = model(**viz_inputs).attentions
sentence_b_start = (viz_inputs.token_type_ids == 0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_inputs.input_ids[0])

head_view(attention, tokens, sentence_b_start, heads=[8])

Downloading:   0%|          | 0.00/420M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


<IPython.core.display.Javascript object>

# The Feed-Forward Layer

🤖 Nos transformers, a subcamada feed-forward no codificador e no decodificador é uma rede neural totalmente conectada de duas camadas. Em vez de processar toda a sequência de embedding (ou tokens) como um único vetor, ela processa cada embedding de forma independente.

💉 Pense sobre diabetes, frequentemente associada a diferentes biomarcadores que podem ser testados a partir de uma amostra de sangue. Várias reações químicas e físicas precisam ser feitas para obter cada biomarcador. Por exemplo, podemos querer avaliar os níveis de glicose, insulina e hemoglobina A1C. Ainda assim, dependendo dos resultados depois que recebemos a saída, devemos avaliar diferentes características de cada biomarcador. A insulina, por exemplo, poderia ser testada usando tolerância à glicose, curvas de insulina, etc. Isso ajudaria a reduzir nossas hipóteses para estar mais próximas de um diagnóstico.

⏩ A camada feed-forward funciona de forma semelhante. Ela pega cada sequência de embedding de forma independente (cada biomarcador) e produz um tensor passado por transformações da camada feed-forward. Isso nos permite capturar padrões mais complexos em nossos dados e reduzir a dimensão dos dados de entrada (reduzir hipóteses em diagnósticos).

# Feed-Forward Layer Code

In [15]:
class FeedForward(nn.Module):
    """Feed-forward network used in the Transformer model.

    This network applies two linear transformations with a GELU activation function
    and dropout regularization to the input tensor.

    Args:
        config (transformers.PretrainedConfig): Configuration class for the model.

    Attributes:
        linear_1 (nn.Linear): First linear transformation layer.
        linear_2 (nn.Linear): Second linear transformation layer.
        gelu (nn.GELU): GELU activation function.
        dropout (nn.Dropout): Dropout regularization layer.

    """
    def __init__(self, config):
        super().__init__()
        self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
        self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
        self.gelu = nn.GELU()
        self.dropout = nn.Dropout(config.hidden_dropout_prob)

    def forward(self, x):
        """Apply the feed-forward network to the input tensor.

        Args:
            x (torch.Tensor): Input tensor of shape (batch_size, sequence_length, hidden_size).

        Returns:
            torch.Tensor: Output tensor of shape (batch_size, sequence_length, hidden_size).

        """
        x = self.linear_1(x)  # Apply the first linear transformation to the input tensor.
        x = self.gelu(x)  # Apply the GELU activation function to the output of the first linear layer.
        x = self.linear_2(x)  # Apply the second linear transformation to the output of the first linear layer.
        x = self.dropout(x)  # Apply dropout regularization to the output of the second linear layer.
        return x


In [16]:
feed_forward = FeedForward(config)
ff_outputs = feed_forward(attn_outputs)
ff_outputs.size()

torch.Size([1, 5, 768])

This was the final ingredient of our encoder layer! 


# Layer Normalization

A arquitetura Transformer utiliza normalização por camada e conexões de atalho (skip connections).

**Layer normalization**: ajusta cada entrada do lote para ter média zero e variância unitária.

**Skip connections**: passa um tensor para a próxima camada do modelo sem processamento, e adiciona ao tensor processado.

Existem dois modos principais de aplicar a camada de normalização

- Post layer normalization (truque para treinar a medida que o gradiente diverge) o learning rate warm-up é usado para ajudar no treinamento
- Pre layer normalization (normalmente usada para dar mais estabilidade durante o treinamento)

### Intuition:

Na medicina, sistemas de pontuação avaliam a saúde de um paciente usando diferentes indicadores. O escore CURB-65 avalia a gravidade da pneumonia usando cinco fatores. O escore padroniza as entradas para facilitar a criação de um plano de ação (semelhante à normalização por camada nos transformers). Se o paciente apresentar vários fatores de risco, podemos usar "conexões de atalho" para focar nos fatores mais importantes e fazer um diagnóstico mais rápido.

<img src="https://learning.oreilly.com/api/v2/epubs/urn:orm:book:9781098136789/files/assets/nlpt_0306.png" width=400>

<img src="https://img.grepmed.com/uploads/747/stratification-management-pneumonia-admission-diagnosis-original.jpeg" width=400 >

# Layer normalization code

In [17]:
class TransformerEncoderLayer(nn.Module):
    """
    Transformer Encoder Layer that applies Multi-Head Attention and Feed-Forward layers with skip connections.

    Args:
        config: a configuration object with various hyperparameters.
    """

    def __init__(self, config):
        super().__init__()

        # initialize two layer normalization layers for the skip connections
        self.layer_norm_1 = nn.LayerNorm(config.hidden_size)
        self.layer_norm_2 = nn.LayerNorm(config.hidden_size)

        # initialize multi-head attention and feed-forward layers
        self.attention = MultiHeadAttention(config)
        self.feed_forward = FeedForward(config)

    def forward(self, x):
        """
        Forward pass of Transformer Encoder Layer.

        Args:
            x: a tensor of shape (batch_size, seq_length, hidden_size) containing input embeddings.

        Returns:
            a tensor of shape (batch_size, seq_length, hidden_size) containing the output embeddings.
        """

        # apply layer normalization to input tensor
        hidden_state = self.layer_norm_1(x)

        # apply multi-head attention with a skip connection
        x = x + self.attention(hidden_state)

        # apply feed-forward layer with a skip connection
        x = x + self.feed_forward(self.layer_norm_2(x))

        return x


Vamos testar o código e ver se ele funciona

In [18]:
encoder_layer = TransformerEncoderLayer(config)
inputs_embeds.shape, encoder_layer(inputs_embeds).size()

(torch.Size([1, 5, 768]), torch.Size([1, 5, 768]))

# Positional Embeddings

Em Transformers, a implementação da camada multi-head attention como uma soma de pesos perda a informação de posição de sequência dos tokens. Para tratar esse problema, o embeddings posicional é adicionado.

📍 Positional embeddings são baseadas aumentar os token embeddings com um padrão de posição. Em resumo, a posição das palavras tem significado.

Para fazer isso, existem três técnicas principais:

1. Learnable positional embeddings (🧠): A posição de cada token na sequência é representado por um vetor de embedding aprendível, que pode ser atualizado durante o treino.

2. Absolute positional representations (🔢): A posição de cada token na sequência é representado por um padrão fixo de sinais senos e cossenos, que codificam a posição absoluta.

3. Relative positional representations (📈): A posição relativa entre os tokens é codificada pela modificação o mecanismo de atenção para levar em consideração a distância entre os tokens da sequência. 

Para essa abordagem, usaremos o índice da posição como entrada.

Para a implementação, coisas para se lembrar:

- ``nn.Embedding`` é usada para criar uma camada de embedding que é uma labela de consulta dado dois argumentos, o tamanho do vocabulário e o número de dimensões do embedding

# Positional Embedding code

In [20]:
class Embeddings(nn.Module):
    def __init__(self, config):
        """
        Initializes the embedding layer used to represent the input sequence as a sequence of hidden states.
        
        Args:
            config (Config): The configuration object that specifies the hyperparameters of the model.
        """
        super().__init__()
        
        # create an embedding layer for token embeddings
        self.token_embeddings = nn.Embedding(config.vocab_size, 
                                            config.hidden_size)
        
        # create an embedding layer for position embeddings
        self.position_embeddings = nn.Embedding(config.max_position_embeddings,
                                               config.hidden_size)
        
        # create a layer normalization layer
        self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12)
        
        # create a dropout layer
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        
    def forward(self, input_ids):
        """
        Performs forward pass on the input sequence.
        
        Args:
            input_ids (torch.Tensor): The input sequence represented as a sequence of token ids.
        
        Returns:
            embeddings (torch.Tensor): The sequence of hidden states generated by the embedding layer.
        """
        
        # create position IDs for input sequence
        seq_length = input_ids.size(1)
        position_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0)
        
        # Create token and position embeddings
        token_embeddings = self.token_embeddings(input_ids)
        position_embeddings = self.position_embeddings(position_ids)
        
        # Combine token and position embeddings
        embeddings = token_embeddings + position_embeddings
        
        # apply layer normalization
        embeddings = self.layer_norm(embeddings)
        
        # apply dropout
        embeddings = self.dropout(embeddings)
        
        return embeddings


Em resumo, a classe Embeddings é usada para inicializar a camada de incorporação que é utilizada para representar a sequência de entrada como uma sequência de estados ocultos. O método forward desta classe recebe a sequência de entrada como entrada e realiza as seguintes operações:

1. Cria IDs de posição para a sequência de entrada.
2. Cria incorporações de token e incorporações de posição para a sequência de entrada usando as respectivas camadas de incorporação.
3. Combina as incorporações de token e incorporações de posição para gerar a sequência de estados ocultos.
4. Aplica normalização por camada à sequência de estados ocultos.
5. Aplica dropout à sequência de estados ocultos.
6. Retorna a sequência de estados ocultos.

In [21]:
embedding_layer = Embeddings(config)
embedding_layer(inputs.input_ids).size()

torch.Size([1, 5, 768])

# Full transformer encoder

Vamos colocar tudo junto combinando os embeddings com a camada de codificação.

In [22]:
class TransformerEncoder(nn.Module):
    """
    Transformer Encoder module that applies the TransformerEncoderLayer to the input tensor.
    """
    def __init__(self, config):
        super().__init__()
        # initialize embeddings layer
        self.embeddings = Embeddings(config)
        # create list of TransformerEncoderLayer instances
        self.layers = nn.ModuleList([TransformerEncoderLayer(config)
                                     for _ in range(config.num_hidden_layers)])
        
    def forward(self, x):
        """
        Perform forward pass through the Transformer Encoder module.
        
        Args:
            x (torch.Tensor): Input tensor with shape [batch_size, sequence_length].
        
        Returns:
            torch.Tensor: Encoded tensor with shape [batch_size, sequence_length, hidden_size].
        """
        # apply embeddings layer
        x = self.embeddings(x)
        # apply each TransformerEncoderLayer instance in layers list
        for layer in self.layers:
            x = layer(x)
        # return encoded tensor
        return x

In [23]:
encoder = TransformerEncoder(config)
encoder(inputs.input_ids).size()

torch.Size([1, 5, 768])

# Adding a Classification Head

🤖 Os Transformers são modelos poderosos que consistem em duas partes - o corpo e a cabeça. O corpo, também conhecido como codificador, não é específico para nenhuma tarefa e pode ser usado em várias tarefas, como classificação de texto, tradução de idiomas e legendagem de imagens. Por outro lado, a cabeça é específica para uma tarefa específica, como classificar um texto em diferentes categorias.

📝 Uma vez que reunimos todas as peças no decodificador, temos o corpo do nosso transformer. No entanto, precisamos atribuí-lo a uma tarefa específica, e é aí que a cabeça entra em jogo. A saída da camada do codificador é o estado oculto de um token específico, geralmente o token [CLS]. Em seguida, colocamos isso no classificador, que é uma camada linear que produz escores para cada rótulo possível na tarefa de classificação. Finalmente, o rótulo com o maior escore é selecionado como o rótulo previsto.

🧩 Ao separar o corpo e a cabeça do transformer, podemos facilmente usar o mesmo corpo para diferentes tarefas simplesmente anexando uma cabeça diferente para cada tarefa. Este design modular nos permite reutilizar o codificador, que é a parte mais computacionalmente cara do transformer, e economiza tempo e recursos.


In [24]:
class TransformerForSequenceClassification(nn.Module):
    """
    A class for performing sequence classification using a Transformer.

    Parameters:
        config (object): Configuration object that contains various hyperparameters for the model.
    """
    def __init__(self, config):
        super().__init__()

        # Initialize a TransformerEncoder object with the given configuration
        self.encoder = TransformerEncoder(config)

        # Instantiate a dropout layer with the dropout probability defined in the configuration
        self.dropout = nn.Dropout(config.hidden_dropout_prob)

        # Instantiate a linear layer that maps from the hidden state size to the number of labels
        self.classifier = nn.Linear(config.hidden_size, config.num_labels)

    def forward(self, x):
        """
        Perform forward pass through the model.

        Parameters:
            x (tensor): Input tensor with shape (batch_size, sequence_length).

        Returns:
            logits (tensor): Output tensor with shape (batch_size, num_labels).
        """
        # Pass the input sequence through the Transformer encoder and get the hidden state of the [CLS] token
        x = self.encoder(x)[:, 0, :]

        # Apply dropout to the hidden state
        x = self.dropout(x)

        # Pass the hidden state through the classifier (linear layer) to get the logits
        logits = self.classifier(x)

        # Return the logits
        return logits

In [25]:
config.num_labels = 3
encoder_classifier = TransformerForSequenceClassification(config)
encoder_classifier(inputs.input_ids).size()

torch.Size([1, 3])

# The Decoder

A principal diferença entre o decodificador e o codificador são as duas camadas de atenção no decodificador.

- **Masked multi-head self-attention layer**: Garante que os tokens que geramos em cada passo de tempo são baseados apenas nas saídas passadas e no token atual sendo previsto. Sem isso, o decodificador poderia trapacear durante o treinamento simplesmente copiando as traduções-alvo; mascarar as entradas garante que a tarefa não seja trivial.

- **Encoder-decoder attention layer**: Realiza atenção multi-cabeça sobre os vetores de chave e valor de saída do conjunto de codificadores, com as representações intermediárias do decodificador atuando como as consultas. Dessa forma, a camada de atenção codificador-decodificador aprende como relacionar tokens de duas sequências diferentes, como dois idiomas diferentes. O decodificador tem acesso às chaves e valores do codificador em cada bloco.

<div style="display:flex">
    <img src="https://raw.githubusercontent.com/nlp-with-transformers/notebooks/48e4a5e5c44b86e1593c0945a49af9675cfd7158/images/chapter03_encoder-zoom.png" style="width: 400px; height: 400px; margin-right: 20px;">
    <img src="https://learning.oreilly.com/api/v2/epubs/urn:orm:book:9781098136789/files/assets/nlpt_0307.png" style="width: 400px; height: 400px;">
</div>



Veja a Implementação do GPT do [Andrej Karpathy](https://www.youtube.com/watch?v=kCc8FmEb1nY)

Vamos incluir masking em nossa camada de self-attention

- Crea uma mask matrix com un's na diagonal inferior e zeros na superior
- Prevenir que cada atenção espiasse tokens futuros usando Tensor.masked_fill() para substituir todos os zeros por menos infinito.


In [26]:
# mask matrix with ones on the lower diagonal and zeros above
seq_len = inputs.input_ids.size(-1)
mask = torch.tril(torch.ones(seq_len, seq_len)).unsqueeze(0)
mask[0]

tensor([[1., 0., 0., 0., 0.],
        [1., 1., 0., 0., 0.],
        [1., 1., 1., 0., 0.],
        [1., 1., 1., 1., 0.],
        [1., 1., 1., 1., 1.]])

In [27]:
# replace all zeros with negative infinty to prevent peeking at the future
scores.masked_fill(mask==0, -float("inf"))

tensor([[[ 2.5910e+01,        -inf,        -inf,        -inf,        -inf],
         [-4.9999e-01,  2.8015e+01,        -inf,        -inf,        -inf],
         [ 2.0758e-01,  2.0850e-02,  3.0182e+01,        -inf,        -inf],
         [ 2.4961e-01, -4.6259e-01,  3.6632e-01,  2.9292e+01,        -inf],
         [-6.8938e-01,  2.1588e+00, -4.4054e-01,  2.6151e-01,  3.1112e+01]]],
       grad_fn=<MaskedFillBackward0>)

Vamos incluir o comportamente de máscara no nosso dot product attention

In [28]:
def scaled_dot_product_attention(query, key, value, mask=None):
    """
    Compute the scaled dot-product attention given the query, key, and value tensors.
    
    Args:
        query (torch.Tensor): A tensor of shape (batch_size, query_len, hidden_size).
        key (torch.Tensor): A tensor of shape (batch_size, key_len, hidden_size).
        value (torch.Tensor): A tensor of shape (batch_size, value_len, hidden_size).
        mask (torch.Tensor): An optional tensor of shape (batch_size, query_len, key_len) representing the mask to be
                             applied to the scores. Default: None.
                             
    Returns:
        A tensor of shape (batch_size, query_len, hidden_size) representing the weighted sum of the value tensor using
        the softmax of the scores.
    """
    # Compute the size of the last dimension of the query tensor
    dim_k = query.size(-1)
    # Compute the scores by performing a batch matrix multiplication between query and the transpose of key
    # Scale the results by the square root of dim_k
    scores = torch.bmm(query, key.transpose(1, 2)) / sqrt(dim_k)
    # Apply the mask to the scores tensor if it is not None
    if mask is not None:
        scores = scores.masked_fill(mask == 0, float("-inf"))
    # Apply the softmax function along the last dimension of the scores tensor to get the attention weights
    weights = F.softmax(scores, dim=-1)
    # Compute the weighted sum of the value tensor using the attention weights
    return weights.bmm(value)


# The Transformer Tree of Life

Imagem que mostra os modelos mais proeminentes e seus descendentes:

- **Encoder-only models**: Esses modelos são projetados para receber uma sequência de entrada e produzir uma única representação dessa sequência. Eles são tipicamente usados para tarefas como classificação de sentenças ou reconhecimento de entidades nomeadas, onde o objetivo é extrair informações de uma sequência dada sem gerar uma nova saída.

- **Decoder-only models**: Esses modelos são projetados para receber uma sequência de entrada codificada e gerar uma sequência de saída token por token. Eles são comumente usados para tarefas como modelagem de linguagem, tradução automática e geração de texto, onde o objetivo é gerar uma nova sequência de tokens com base na entrada.

- **Encoder-decoder models**: Esses modelos combinam as arquiteturas de codificador e decodificador, permitindo que eles recebam uma sequência de entrada e gerem uma sequência de saída com base nessa entrada. Eles são comumente usados para tarefas como tradução automática e sumarização, onde o objetivo é gerar uma nova sequência com base em uma sequência de entrada.

<img src="https://learning.oreilly.com/api/v2/epubs/urn:orm:book:9781098136789/files/assets/nlpt_0308.png">